In [ ]:
from google.colab import drive

drive.mount("/content/drive")

Mounted at /content/drive


In [ ]:
import os
import cv2
import glob
import random
import numpy as np
import tensorflow as tf

import matplotlib.pyplot as plt
import tensorflow.keras.backend as K

from tensorflow.keras.layers import Conv2D
from tensorflow.keras.models import Model
from tensorflow.keras.models import load_model
from tensorflow.keras.preprocessing.image import load_img
from tensorflow.keras.utils import img_to_array, get_file
from tensorflow.keras.applications.efficientnet import preprocess_input

In [ ]:
@tf.custom_gradient
def customRelu(x):
    def backpropGrads(dx):
        return tf.cast(dx > 0, "float32") * tf.cast(x > 0, "float32") * dx

    return tf.nn.relu(x), backpropGrads


class SaliencyMap:
    def __init__(self, model, img_path, layer_name=None):
        self.model = model
        self.img_path = img_path
        self.target_size = self.model.input_shape[1:]

        self.layer_name = layer_name
        if self.layer_name == None:
            for layer in reversed(model.layers):
                if isinstance(layer, Conv2D):
                    self.layer_name = layer.name
                    break

    def img_preprocessor(self):
        image = load_img(path=self.img_path, target_size=self.target_size)
        img_array = img_to_array(image, dtype="float32")
        img_array = tf.expand_dims(img_array, axis=0)
        img_array = preprocess_input(img_array)
        return image, img_array

    def gradModel(self):
        _, img_array = self.img_preprocessor()
        grad_model = Model(
            inputs=[self.model.inputs],
            outputs=[self.model.get_layer(self.layer_name).output, self.model.output],
        )

        convOuts, probs = grad_model(img_array)
        return convOuts, probs

    def guidedBackpropModel(self):
        guided_backprop_model = Model(
            inputs=[self.model.inputs],
            outputs=[self.model.get_layer(self.layer_name).output],
        )
        # populate the list with layers with activation functions
        activated_layers = [
            layer
            for layer in guided_backprop_model.layers
            if hasattr(layer, "activation")
        ]

        for layer in activated_layers:
            if (
                layer.activation == tf.keras.activations.relu
            ):  # used to modify the relu with our custom relu activation
                layer.activation = customRelu  # applies relu both in the forward and backward pass(unlike the regular relu which is active in the forward pass)
        return guided_backprop_model

    def GradCAM(self, class_index=None):

        with tf.GradientTape() as tape:
            convOuts, probs = self.gradModel()
            if class_index == None:
                class_index = int(
                    np.argmax(probs)
                )  # returns the index of the maximum value
            class_prob = probs[:, class_index]

        grads = tape.gradient(class_prob, convOuts)
        convOuts, grads = convOuts[0], grads[0]  # discard batch

        weights = tf.reduce_mean(grads, axis=(0, 1))
        gradcam = tf.reduce_sum(
            tf.multiply(weights, convOuts), axis=-1
        )  # combine along the channel dimension and add the values
        gradcam = tf.maximum(gradcam, 0)  # final result.(relu)

        gradcam /= np.max(gradcam.numpy())  # Normalization
        gradcam = np.uint8(gradcam * 255)  # scale between 0-255

        gradcam = cv2.resize(gradcam, self.target_size[:-1], cv2.INTER_LINEAR)
        gradcam = cv2.applyColorMap(gradcam, cv2.COLORMAP_JET)

        return gradcam

    def GradCAMPlus(self, class_index=None):
        with tf.GradientTape() as tape1:
            with tf.GradientTape() as tape2:
                with tf.GradientTape() as tape3:
                    convOuts, probs = self.gradModel()
                    if class_index == None:
                        class_index = int(np.argmax(probs[0]))
                    class_prob = probs[:, class_index]

                    first_grad = tape3.gradient(class_prob, convOuts)
                second_grad = tape2.gradient(first_grad, convOuts)
            third_grad = tape1.gradient(second_grad, convOuts)

        convOuts, first_grad, second_grad, third_grad = (
            convOuts[0],
            first_grad[0],
            second_grad[0],
            third_grad[0],
        )  # discard batch

        # compute alpha
        global_sum = tf.reduce_sum(convOuts, axis=(0, 1))
        alpha_numer = second_grad
        alpha_denom = (2.0 * second_grad) + (third_grad * global_sum) + 1e-10
        alpha = alpha_numer / alpha_denom

        # compute weights
        weights = tf.reduce_sum(
            tf.multiply(alpha, tf.maximum(first_grad, 0.0)), axis=(0, 1)
        )
        gradcam_pp = tf.reduce_sum(
            tf.multiply(weights, convOuts), axis=-1
        )  # combine along the channel dimension
        gradcam_pp = tf.maximum(gradcam_pp, 0)  # final result.(relu)

        gradcam_pp /= np.max(gradcam_pp.numpy())  # Normalization
        gradcam_pp = np.uint8(gradcam_pp * 255)  # scale between 0-255

        gradcam_pp = cv2.resize(gradcam_pp, self.target_size[:-1], cv2.INTER_LINEAR)
        gradcam_pp = cv2.applyColorMap(gradcam_pp, cv2.COLORMAP_JET)

        return gradcam_pp

    def GuidedBackProp(self, heatmap=True):
        _, img_array = self.img_preprocessor()
        guided_backprop_model = self.guidedBackpropModel()

        with tf.GradientTape() as tape:
            convIns = img_array
            tape.watch(convIns)
            convOuts = guided_backprop_model(convIns)

        grads = tape.gradient(convOuts, convIns)[0]

        saliency_map = cv2.resize(
            np.asarray(grads), self.target_size[:-1], cv2.INTER_LINEAR
        )
        if heatmap:
            saliency_map = self.deprocessImage(saliency_map)
            return saliency_map
        return saliency_map

    def GuidedGradcam(self):

        gb_gradcam = np.multiply(
            np.float32(self.GuidedBackProp(heatmap=False)), np.float32(self.GradCAM())
        )
        gb_gradcam = self.deprocessImage(gb_gradcam)
        gb_gradcam = cv2.cvtColor(gb_gradcam, cv2.COLOR_BGR2RGB)
        return gb_gradcam

    def GuidedGradcamPlus(self):
        gb_gradcamP = np.multiply(
            np.float32(self.GuidedBackProp(heatmap=False)),
            np.float32(self.GradCAMPlus()),
        )
        gb_gradcamP = self.deprocessImage(gb_gradcamP)
        gb_gradcamP = cv2.cvtColor(gb_gradcamP, cv2.COLOR_BGR2RGB)
        return gb_gradcamP

    # def overlayImage(self, heatmap):
    #   img, _ = self.img_preprocessor()

    #   overlayed_img = (0.5 * np.uint8(img)) + (0.3 * heatmap)
    #   overlayed_img /= np.max(overlayed_img)
    #   overlayed_img *= 255
    #   return np.uint8(overlayed_img)

    def overlayImage(self, heatmap):
        img, _ = self.img_preprocessor()

        overlayed_img = (0.5 * np.uint8(img)) + (0.3 * heatmap)
        overlayed_img /= np.max(overlayed_img)
        overlayed_img *= 255
        overlayed_img = cv2.cvtColor(np.uint8(overlayed_img), cv2.COLOR_BGR2RGB)
        return overlayed_img

    def overlayText(self, heatmap, class_index=None, class_label=None):
        overlayed_img = self.overlayImage(heatmap)
        _, probs = self.gradModel()

        if class_index == None:
            class_index = int(np.argmax(probs[0]))
        class_prob = probs[:, class_index].numpy().item()

        _text = f"{class_label[class_index].capitalize()}- {class_prob*100:.4f}%"
        overlayed_img = cv2.putText(
            img=overlayed_img,
            text=_text,
            org=(5, 15),
            fontFace=cv2.FONT_HERSHEY_SIMPLEX,
            fontScale=0.7,
            color=(0, 0, 0),
            thickness=1,
        )

        return overlayed_img

    def deprocessImage(self, img_array):

        img_array -= img_array.mean()
        img_array /= img_array.std() + 1e-07
        img_array *= 0.25
        img_array += 0.5
        img_array *= 255
        img_array = np.clip(img_array, 0, 255).astype("uint8")
        return img_array

In [ ]:
__model = load_model("/content/drive/MyDrive/CoffeeDiseaseClassifier/BestModel")
train_dir = "/content/drive/MyDrive/CoffeeDiseaseClassifier/CoffeeDeseaseDatasets/train"

In [ ]:
class_labels = os.listdir(train_dir)
fig, ax = plt.subplots(5, 6, figsize=(30, 20), subplot_kw={"xticks": [], "yticks": []})
for i, label in enumerate(class_labels):

    file_len = len(glob.glob(os.path.join(train_dir, label) + "/*.jpg"))
    rand_idx = random.randint(0, file_len)

    file_path = glob.glob(os.path.join(train_dir, label) + "/*.jpg")[
        rand_idx
    ]  # take one image from each directory
    img = load_img(file_path, target_size=(224, 224))

    # heatmap = SaliencyMap(model=__model, img_path=file_path, layer_name='top_conv')
    heatmap = SaliencyMap(model=__model, img_path=file_path)
    maps = [
        img,
        heatmap.overlayImage(heatmap.GradCAMPlus()),
        heatmap.overlayImage(heatmap.GradCAM()),
        heatmap.GuidedGradcamPlus(),
        heatmap.GuidedBackProp(),
        heatmap.GuidedGradcam(),
    ]
    titles = [
        "Original",
        "Gradcam++",
        "Gradcam",
        "Guided Gradcam++",
        "Guided Backprop",
        "Guided Gradcam",
    ]
    for j, map in enumerate(maps):
        ax[i, j].set_title(str(titles[j]), fontsize=18)
        ax[i, j].set_ylabel(str(class_labels[i]), fontsize=18)
        ax[i, j].imshow(map)

plt.tight_layout()
plt.show()

In [ ]:
class_labels = os.listdir(train_dir)
fig, ax = plt.subplots(
    5, 6, sharey=True, figsize=(30, 20), subplot_kw={"xticks": [], "yticks": []}
)
for i, label in enumerate(class_labels):
    file_len = len(
        glob.glob(os.path.join(train_dir, label) + "/*.jpg")
    )  # random file picking
    rand_idx = random.randint(0, file_len)

    file_path = glob.glob(os.path.join(train_dir, label) + "/*.jpg")[rand_idx]
    img = np.uint8(load_img(file_path, target_size=(224, 224)))
    img = cv2.putText(
        img=img,
        text=f"Truth- {label.capitalize()}",
        org=(5, 15),
        fontFace=cv2.FONT_HERSHEY_SIMPLEX,
        fontScale=0.7,
        color=(0, 0, 0),
        thickness=1,
    )

    heatmap = SaliencyMap(model=__model, img_path=file_path, layer_name="top_conv")
    maps = [
        img,
        heatmap.overlayText(heatmap.GradCAM(0), 0, class_labels),
        heatmap.overlayText(heatmap.GradCAM(1), 1, class_labels),
        heatmap.overlayText(heatmap.GradCAM(2), 2, class_labels),
        heatmap.overlayText(heatmap.GradCAM(3), 3, class_labels),
        heatmap.overlayText(heatmap.GradCAM(4), 4, class_labels),
    ]

    for j, map in enumerate(maps):
        ax[i, j].imshow(map)

plt.tight_layout()
plt.show()